In [2]:
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go

In [356]:
def generate_animation(fixed_path, animated_path, hover_text, title = None):
    animation_frames = []
    for i in range(0, len(animated_path)):
        seg = animated_path*0
        seg[:i+1] = animated_path[:i+1]
        seg[i+1:] = seg[i]
        opacity = np.ones(len(seg))*1.0
        opacity[i] = 1.0
        size = np.ones(len(seg))*3
        size[i] = 12
        #marker_color=[(lambda x: f'rgba(200, 50, 50, {x})')(x) for x in opacity]
        animation_frames.append(go.Frame(data=
            [  
                go.Scatter(x=seg[:,0], y = seg[:,1],
                    marker_color=[(lambda x: f'rgba(200, 50, 50, {x})')(x) for x in opacity],
                    marker_size=size,
                    mode='markers',
                    hovertemplate =
                    '<br><b>X</b>: %{x}'+
                    '<br><b>Y</b>: %{y}'+
                    '<br><b>Data</b>: %{text}',
                    text=hover_text
                    #line_color='rgba(200, 50, 50, 0.1)',
                ),
                go.Scatter(x=fixed_path[:,0], y = fixed_path[:,1],
                    marker_color='rgba(50, 50, 200, 1.0)',
                    line_color='rgba(50, 50, 200, 0.8)',
                )
            ], name=str(i)))
    
    

    fig = go.Figure(
        data=[go.Scatter(x=[0, 0], y=[0, 0],
                    marker_color='rgba(200, 50, 50, 1.0)',
                    line_color='rgba(200, 50, 50, 0.8)',
                    text=hover_text
                ),             
            go.Scatter(x=fixed_path[:,0], y = fixed_path[:,1],
                    marker_color='rgba(50, 50, 200, 1.0)',
                    line_color='rgba(50, 50, 200, 0.8)',
                )],
        layout=go.Layout(
            xaxis=dict(range=[min(min(fixed_path[:,0]), min(animated_path[:,0]))-1, max(max(fixed_path[:,0]), max(animated_path[:,0]))+1], autorange=False),
            yaxis=dict(range=[min(min(fixed_path[:,1]), min(animated_path[:,1]))-1, max(max(fixed_path[:,1]), max(animated_path[:,1]))+1], autorange=False),
            title=title,
            updatemenus=[
        {
            "buttons": [
                {
                    "args": [None, {"frame": {"duration": 10, "redraw": False},
                                    "fromcurrent": False, "transition": {"duration": 0,
                                                                        "easing": "linear"}}],
                    "label": "Play",
                    "method": "animate"
                },
                {
                    "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                    "mode": "immediate",
                                    "transition": {"duration": 0}}],
                    "label": "Pause",
                    "method": "animate"
                }
            ],
            "direction": "left",
            "pad": {"r": 10, "t": 87},
            "showactive": False,
            "type": "buttons",
            "x": 0.1,
            "xanchor": "right",
            "y": 0,
            "yanchor": "top"
        }
    ]
        ),
        frames=animation_frames
    )

    slider_dict = {
        "active": 0,
        "yanchor": "top",
        "xanchor": "left",
        "currentvalue": {
            "font": {"size": 20},
            "prefix": "Time Step:",
            "visible": True,
            "xanchor": "left"
        },
        "transition": {"duration": 10, "easing": "linear"},
        "pad": {"b": 10, "t": 50},
        "len": 0.9,
        "x": 0.1,
        "y": 0,
        "steps": [
            (lambda x: 
                {  
                    "args": [
                        [x],
                        {"frame": {"duration": 10, "redraw": False},
                                    "fromcurrent": False, "mode": "immediate", "transition": {"duration": 0,
                                                                        "easing": "linear"}}
                    ],
                    "label": x,
                    "method": "animate"
                }
            )(x) for x in range(0, len(animation_frames), max(1, len(animation_frames)//30))
        ]
    }
    fig.update_layout(sliders=[slider_dict], height=800, width=800)
    fig.update_yaxes(
        scaleanchor="x",
        scaleratio=1,
    )
    fig.show()

In [328]:
def get_proj_offset(point, path):
    rel = point-path[:-1]
    vecs = path[1:]-path[:-1]
    norm_squared = np.sum(vecs*vecs, axis=-1)
    proj_base = (np.sum(rel*vecs, axis=-1)/norm_squared).reshape(-1,1)
    proj = proj_base*vecs
    proj_short = np.where(proj_base > 0, np.maximum(proj_base-1, 0), proj_base)*vecs+(rel-proj)
    seg = np.argmin(np.linalg.norm(proj_short, axis=-1))
    offset = proj_short[seg]
    direction0 = vecs[seg]/np.sqrt(norm_squared[seg])
    direction1 = vecs[min(len(vecs)-1, seg+1)]/np.sqrt(norm_squared[min(len(vecs)-1, seg+1)])
    prop = proj_base[seg]
    return offset, direction0, direction1, prop, seg

In [363]:
fixed_path = np.array([[-1,0], [0,1], [1,1], [3,2], [5,2], [6,1]])
X = np.array([0,0])
Xp = np.array([0,0])
Xpp = np.array([0,0])

travel_history = []
direction_history = []
offset_history = []
max_steps = 400
eps0 = 0.01
dt = 0.3
noising = 0.0
#noise_rate = 0.01
speed_mod = 1.0
alpha_0 = 0.1
alpha_1 = 0.3**2
alpha_3 = 0.4

pre_turn = 0.4

while (np.linalg.norm(X-fixed_path[-1]) > eps0) and (len(travel_history) < max_steps):
    travel_history.append(X)
    offset, c_direction, n_direction, prop, seg = get_proj_offset(X.reshape(1,-1), fixed_path)
    if((prop < 1.0) and (prop > 1.0-pre_turn)):
        direction = ((c_direction*(1.0-prop))+(n_direction*(prop-(1.0-pre_turn))))/(pre_turn)
    else:
        direction = c_direction
    direction_history.append(direction)
    X = X+Xp*dt+np.random.normal(0.0, noising*np.linalg.norm(Xp), 2)#*np.random.binomial(1, noise_rate)
    Xp = Xp+Xpp*dt
    if(seg != len(fixed_path)-2):
        Xpp = ((direction*speed_mod-Xp)*alpha_0)-(offset*alpha_1)-(Xp*alpha_3)
        offset_history.append(offset)
    else:
        Xpp = -((X-fixed_path[-1])*(alpha_1))-(Xp*(alpha_3**0.5))
        offset_history.append((X-fixed_path[-1])*np.linalg.norm(X-fixed_path[-1]))
    
travel_history = np.array(travel_history)
generate_animation(fixed_path, travel_history, np.array(direction_history).astype(str), title='No Noise')